# PART 4: NAVIGATION ANALYSIS

**Objective:** This notebook will implement technician-navigation to study the potential benefits in productivity and operational costs.

---

In [74]:
# Data Management
import pandas as pd
import pickle

# Data Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Navigation Application
from uc_navigator import *

# Utils
import ast
import warnings
from itertools import product
import pprint
from random import choice, choices, shuffle, randrange
from time import sleep
%matplotlib inline
sns.set_style('white')
sns.set_color_codes()
plt.style.use('default')
warnings.filterwarnings("ignore")
pp = pprint.PrettyPrinter(indent=0)

---
---

## 4A: Setup

**Objective**: Read in the clinic data & necessary patient records files.

---

In [75]:
past_patients_df = pd.read_pickle('./pickled_objects/past_patients_df.pkl')
past_patients_df.head()

datetime         pt_name      pt_dob  pt_age  \
pt_id                                                              
4000001  2021-05-01 08:03:20    Erica Nguyen  1971-11-14      50   
4000008  2021-05-01 08:05:02   Zachary Brown  1978-11-24      43   
4000010  2021-05-01 08:07:25    Sheila Miles  2006-12-10      15   
4000002  2021-05-01 08:07:48  Spencer Mendez  1944-01-11      78   
4000011  2021-05-01 08:12:08  Rachael Larson  2003-01-16      19   

        visit_location        visit_reason  visit_code  visit_date visit_day  \
pt_id                                                                          
4000001           rino  weakness/dizziness           5  2021-05-01  Saturday   
4000008           rino      cold/flu/fever           4  2021-05-01  Saturday   
4000010           rino          covid-test           4  2021-05-01  Saturday   
4000002           rino  weakness/dizziness           5  2021-05-01  Saturday   
4000011           rino          covid-test           4  2021-05-01  Saturday   

        checkin_time  ... assigned_num_techs  needed_num_techs  weekend  hour  \
pt_id                 ...                                                       
4000001     08:03:20  ...                  3                 1        1     8   
4000008     08:05:02  ...                  3                 1        1     8   
4000010     08:07:25  ...                  3                 1        1     8   
4000002     08:07:48  ...                  3                 2        1     8   
4000011     08:12:08  ...                  3                 2        1     8   

         denver  edgewater lakewood  rino  wheatridge  new_num_techs  
pt_id                                                                 
4000001       0          0        0     1           0              2  
4000008       0          0        0     1           0              2  
4000010       0          0        0     1           0              2  
4000002       0          0        0     1           0              2  
4000011       0          0        0     1           0              2  

[5 rows x 23 columns]

In [76]:
new_patients_df = pd.read_pickle('./pickled_objects/new_patients_df.pkl')
new_patients_df.head()

datetime          pt_name      pt_dob  pt_age  \
pt_id                                                               
4020304  2022-05-01 08:00:14  Shannon Lambert  2021-07-22       0   
4020316  2022-05-01 08:03:20     Andrew Lewis  1971-10-26      50   
5022937  2022-05-01 08:07:29   Heather Knight  1956-07-14      65   
5022940  2022-05-01 08:09:25      Emily Brown  1985-02-20      37   
4020310  2022-05-01 08:13:20   Jennifer Colon  1993-10-06      28   

        visit_location visit_reason  visit_code  visit_date visit_day  \
pt_id                                                                   
4020304           rino     ear-pain           4  2022-05-01    Sunday   
4020316           rino  vaccination           3  2022-05-01    Sunday   
5022937       lakewood  vaccination           3  2022-05-01    Sunday   
5022940       lakewood        cough           4  2022-05-01    Sunday   
4020310           rino  sore-throat           4  2022-05-01    Sunday   

        checkin_time  ... assigned_num_techs  needed_num_techs  weekend  hour  \
pt_id                 ...                                                       
4020304     08:00:14  ...                  4                 1        1     8   
4020316     08:03:20  ...                  4                 1        1     8   
5022937     08:07:29  ...                  3                 1        1     8   
5022940     08:09:25  ...                  3                 1        1     8   
4020310     08:13:20  ...                  4                 1        1     8   

         denver  edgewater lakewood  rino  wheatridge  new_num_techs  
pt_id                                                                 
4020304       0          0        0     1           0              3  
4020316       0          0        0     1           0              3  
5022937       0          0        1     0           0              2  
5022940       0          0        1     0           0              2  
4020310       0          0        0     1           0              3  

[5 rows x 23 columns]

In [77]:
clinics_df = pd.read_csv('./fabricated_data/uc_clinics.csv', index_col='branch_name')
clinics_df['nearby_clinics'] = clinics_df.nearby_clinics.apply(lambda x: ast.literal_eval(x))  # ensure correct format of list
clinics_df

lat         lon  to_denver  to_edgewater  to_wheatridge  \
branch_name                                                                  
denver       39.739064 -104.989697          0            12             14   
edgewater    39.753954 -105.067788         14             0              5   
wheatridge   39.766857 -105.081983         14             5              0   
rino         39.767328 -104.981132          6            14             14   
lakewood     39.704552 -105.079883         12             8              8   

             to_rino  to_lakewood  \
branch_name                         
denver             7           14   
edgewater         12            9   
wheatridge        10            9   
rino               0           14   
lakewood          12            0   

                                                nearby_clinics  
branch_name                                                     
denver       [(rino, 7.0), (edgewater, 12.0), (wheatridge, ...  
edgewater    [(wheatridge, 5.0), (lakewood, 9.0), (rino, 12...  
wheatridge   [(edgewater, 5.0), (lakewood, 9.0), (rino, 10....  
rino         [(denver, 6.0), (edgewater, 14.0), (wheatridge...  
lakewood     [(edgewater, 8.0), (wheatridge, 8.0), (denver,...

In [78]:
model = pickle.load(open('./pickled_objects/rf_model.pkl', 'rb'))

---
---

## 4B: Navigation Optimization

**Objective**: Evaluate technician navigation based on manual tuning of parameters.

---

#### Setup "grid-search" for navigation parameters: 

In [79]:
app_param_grid = {
    'ratio': [2, 3, 4], 
    'techs_to_start': [-1, -2],
    'rolling_code': [0, 4.2, 4.4, 4.6]
}

# Cartesian product of parameter options
param_combinations = product(*app_param_grid.values())

A parameter grid was setup to iterate through each potential combination. 
- `ratio` indicates the patient-to-tech ratio to be scheduled and maintained. 
- `techs_to_start` is the change to implement in the initial scheduling (starting each location with 1 or 2 less technicians)
- `rolling_code` is the average severity code at each clinic to use for triggering a transfer

#### Setup results tracker:

In [80]:
results = dict()
for combo in param_combinations:
    results[combo] = {'potential_transfers': 0, 'num_transfers': 0, 'retransfers': 0, 'within_ratio': 0, 'availability_zero': 0, 'availability_one': 0, 'initial_wages': 0, 'modified_wages': 0, 'wages_saved': 0}
# results

Above, a dictionary was created with each possible combination of parameters to store results from conducting the grid-search below. The evaluation metrics of the grid-search were chosen meticulously. Their purpose is to help a client decide which parameters are best for their business model and clinical needs. The following metrics are important evaluators of the TecNav application: potential number of transfers, number of transfers, percentage of transfers that were reversed within an hour, percentage of instances that adhere to the ideal ratio, percentage of transfers that could not be fulfilled, and instances where the availability at another clinic is of only one technician. In addition to these, wage information was also tracked to evaluate some client-based success metrics.

#### Iterate through and evaluate each parameter combination:

In [81]:
# Iterate through each parameter combination
for i in results.keys():

    print(f'\n---------TESTING PARAM COMBO: {i}--------\n')

    ratio, delta, code = i[0], i[1], i[2]
    
    # Assign technicians based on peak hour and specified {ratio}
    aggregated_df = new_patients_df.groupby(['visit_date', 'visit_location']).max()[['rolling_ct']].reset_index(drop=False)
    aggregated_df['assigned_num_techs'] = aggregated_df['rolling_ct'].apply(lambda x: int(x/ratio)+1 if x%ratio != 0 else int(x/ratio))
    schedule_zipper = zip(aggregated_df.visit_date, aggregated_df.visit_location, aggregated_df.assigned_num_techs)
    schedule_dict = {}
    for j in schedule_zipper:
        schedule_dict[(j[0], j[1])] = j[2]
    new_patients_df['assigned_num_techs'] = new_patients_df[['visit_date', 'visit_location']] \
        .apply(lambda x: (x[0], x[1]), axis=1) \
        .map(schedule_dict)
    
    # Schedule {delta} less technicians to begin each day
    new_patients_df['new_num_techs'] = new_patients_df['assigned_num_techs'] + i[1]

    for date in new_patients_df.visit_date.unique():
        df = new_patients_df[new_patients_df.visit_date == date].copy()

        # Execute navigation with modified data and code parameter
        nav = TecNav(df, clinics_df, model, code)
        nav.execute_navigation()

        # Update dataframe with number of technicians at any given point due to navigation
        df['current_num_techs'] = nav.current_num_techs_col
        # Update dataframe with computed staff ratio at any given point due to navigation
        df['ratio'] = df['rolling_ct'] / df['current_num_techs']

        # Gather evaluation metric results from navigation
        results[i]['num_transfers'] += (len(nav.movements))                     # Track total number of movements
        results[i]['retransfers'] += nav.moves_within_hour                      # Track instances that required reverse-transfer within hour 
        within_ratio = (df['ratio'] <= ratio).sum()
        results[i]['within_ratio'] += within_ratio                              # Track proportion of instances within threshold ratio
        avail_one = len(df[df.current_num_techs - df.needed_num_techs == 1])
        results[i]['potential_transfers'] += nav.potential_move                 # Track proportion of instances where availability is 1
        results[i]['availability_one'] += avail_one                             # Track proportion of instances where availability is 1
        results[i]['availability_zero'] += nav.stag                             # Track proportion of instances where availability is 1

        # Profit calculation 
        initial_wages = aggregated_df[aggregated_df.visit_date == date].assigned_num_techs.sum() * 12 * 21
        modified_wages = (aggregated_df[aggregated_df.visit_date == date].assigned_num_techs + delta).sum() * 12 * 21
        wages_saved = initial_wages - modified_wages
        results[i]['initial_wages'] += initial_wages                            # Track wage expenditure without original schedule modification
        results[i]['modified_wages'] += modified_wages                          # Track wage expenditure with navigation-based schedule modification
        results[i]['wages_saved'] += wages_saved                                # Track wage savings


---------TESTING PARAM COMBO: (2, -1, 0)--------


---------TESTING PARAM COMBO: (2, -1, 4.2)--------


---------TESTING PARAM COMBO: (2, -1, 4.4)--------


---------TESTING PARAM COMBO: (2, -1, 4.6)--------


---------TESTING PARAM COMBO: (2, -2, 0)--------

08:46:13 - Edgewater Clinic needs a technician
- Availability:  ['Wheatridge', 'Lakewood', 'Rino']
- Assessing if Wheatridge is a feasible location to pull technician from.
- Pull technician from nearest clinic: Wheatridge, 2 available
- Technician from Wheatridge left at 08:48:49
- Technician from Wheatridge arrived at Edgewater at 08:58:06
- Edgewater: before count = 1 | after count = 2
- Wheatridge: before count = 3 | after count = 2

10:28:39 - Rino Clinic needs a technician
- Availability:  ['Denver', 'Wheatridge', 'Lakewood']
- Assessing if Denver is a feasible location to pull technician from.
- Pull technician from nearest clinic: Denver, 2 available
- Technician from Denver left at 10:30:49
- Technician from Denver arriv

#### Analyze navigation grid search:

In [82]:
# Store results in dataframe
results_df = pd.DataFrame(results).T
results_df.index = results_df.index.values

results_df['within_ratio'] = results_df.within_ratio.apply(lambda x: round(x/len(new_patients_df)*100, 1))
results_df['availability_one'] = results_df.availability_one.apply(lambda x: round(x/len(new_patients_df)*100, 1))
results_df['availability_zero'] = results_df[['potential_transfers', 'availability_zero']].apply(lambda x: round(x[1] / x[0] * 100, 1), axis=1)

results_df = results_df[['potential_transfers', 'num_transfers', 'retransfers', 'within_ratio',
       'availability_zero', 'availability_one', 'initial_wages',
       'modified_wages', 'wages_saved']]
results_df

potential_transfers  num_transfers  retransfers  within_ratio  \
(2, -1, 0.0)                    0              0            0          92.9   
(2, -1, 4.2)                    0              0            0          92.9   
(2, -1, 4.4)                    0              0            0          92.9   
(2, -1, 4.6)                    0              0            0          92.9   
(2, -2, 0.0)                  253            149            0          74.7   
(2, -2, 4.2)                  154            117            0          74.2   
(2, -2, 4.4)                   75             50            0          73.8   
(2, -2, 4.6)                   33             25            0          73.5   
(3, -1, 0.0)                  685            241            0          91.7   
(3, -1, 4.2)                  469            200            0          91.0   
(3, -1, 4.4)                  220             89            0          89.6   
(3, -1, 4.6)                   96             44            0          89.4   
(3, -2, 0.0)                 3325             70            0          56.6   
(3, -2, 4.2)                 2406             46            0          56.7   
(3, -2, 4.4)                 1273             28            0          56.3   
(3, -2, 4.6)                  637             24            0          56.1   
(4, -1, 0.0)                 2819             90            0          82.3   
(4, -1, 4.2)                 2031             71            0          83.6   
(4, -1, 4.4)                 1057             37            0          83.6   
(4, -1, 4.6)                  524             27            0          83.6   
(4, -2, 0.0)                 4368              0            0          35.6   
(4, -2, 4.2)                 3103              0            0          35.6   
(4, -2, 4.4)                 1711              0            0          35.6   
(4, -2, 4.6)                  852              0            0          35.6   

              availability_zero  availability_one  initial_wages  \
(2, -1, 0.0)                NaN              24.8         198828   
(2, -1, 4.2)                NaN              24.8         198828   
(2, -1, 4.4)                NaN              24.8         198828   
(2, -1, 4.6)                NaN              24.8         198828   
(2, -2, 0.0)               41.1              36.6         198828   
(2, -2, 4.2)               24.0              35.4         198828   
(2, -2, 4.4)               33.3              33.6         198828   
(2, -2, 4.6)               24.2              32.7         198828   
(3, -1, 0.0)               64.8              36.1         139860   
(3, -1, 4.2)               57.4              35.7         139860   
(3, -1, 4.4)               59.5              35.8         139860   
(3, -1, 4.6)               54.2              35.3         139860   
(3, -2, 0.0)               97.9              17.2         139860   
(3, -2, 4.2)               98.1              16.4         139860   
(3, -2, 4.4)               97.8              16.2         139860   
(3, -2, 4.6)               96.2              16.1         139860   
(4, -1, 0.0)               96.8              22.3         109368   
(4, -1, 4.2)               96.5              21.5         109368   
(4, -1, 4.4)               96.5              21.6         109368   
(4, -1, 4.6)               94.8              21.4         109368   
(4, -2, 0.0)              100.0               3.1         109368   
(4, -2, 4.2)              100.0               3.1         109368   
(4, -2, 4.4)              100.0               3.1         109368   
(4, -2, 4.6)              100.0               3.1         109368   

              modified_wages  wages_saved  
(2, -1, 0.0)          159768        39060  
(2, -1, 4.2)          159768        39060  
(2, -1, 4.4)          159768        39060  
(2, -1, 4.6)          159768        39060  
(2, -2, 0.0)          120708        78120  
(2, -2, 4.2)          120708        78120  
(2, -2, 4.4)          120708 

A manual grid-search was conducted based on different parameters to gauge the performance of the navigator for 1 month of test data (May 2022).

If the primary client motive is to minimize expenditure and maximize savings, the grid search results recommend increasing the maintained ratio of patients-to-techs, while scheduling 2 less initial techs to begin each day. However, this extreme measure would result in overworked technicians and yields a lower percentage of threshold adherence. On the opposide side of the spectrum, if the client prefers to implement a navigation system that strictly adheres to a pre-determined staff ratio, TecNav recommends maintaining two or three patients per technician and scheduling a higher number of technicians to begin the day. 

On a more balanced scale, the grid-search above shows a 3:1 ratio, scheduling 1 less technician to start the day at each location, and not implementing rolling code as the ideal set of parameters `(3, -1, 0)`. In this scenario, it leads to 241 total transfers for the month that were triggered based on 685 total potential transfers. While 64.8% of potential transfer scenarios were unconverted to actual transfers, this conservative approach yielded 0 retransfers. This means there were no scenarios where a technician was borrowed from a clinic, with that clinic requiring extra help within an hour of giving up that technician. This is also a strong indicator of the potency of the machine learning model that is being evaluated on a more practical metric here. Essentially, the model is doing a thorough job of preventing the need for retransfers by accurately anticipating clinical needs before removing a technician. Lastly, a 91.7% adherance to the specified ratio indicates strong performance of the navigator application with these parameters, that is scheduling 5 less total technicians every day, and still maintaining an appropriate ratio without overwhelming staff. 

Lastly, the initial wages were computed based on the scheduling that would have occurred with the specified ratio. As anticipated, maitaining a lower ratio would increase expenditure (and the corresponding modified wage due to the navigation). While scheduling 2 less technicians at each location to start the day is appealing in terms of the wages saved, this would lead to poor performance in other areas such as the ratio adherence and number of transfers. It is important to note here that even when wages saved are the same for two different parameter combinations, the expenditure can vary based on the scheduled number of technicians.

Overall, the grid search helped inform the specific parameter values to use, for building a recommendation guide for any potential client. Based on these results, and client-provided preferences, the navigator application can be customized to fit their needs. For the purpose of this analysis, `(3, -1, 0)` will be used to build the prototype dashboard to demonstrate to clients.

---
---

## 4C: Navigation Analysis

**Objective**: Deeper exploration into best parameter combination.

---

#### Execute navigation with best parameters:

In [83]:
# Assign technicians based on peak hour and specified {ratio}
aggregated_df = new_patients_df.groupby(['visit_date', 'visit_location']).max()[['rolling_ct']].reset_index(drop=False)
aggregated_df['assigned_num_techs'] = aggregated_df['rolling_ct'].apply(lambda x: int(x/3)+1 if x%3 != 0 else int(x/3))
schedule_zipper = zip(aggregated_df.visit_date, aggregated_df.visit_location, aggregated_df.assigned_num_techs)
schedule_dict = {}
for j in schedule_zipper:
    schedule_dict[(j[0], j[1])] = j[2]
new_patients_df['assigned_num_techs'] = new_patients_df[['visit_date', 'visit_location']] \
    .apply(lambda x: (x[0], x[1]), axis=1) \
    .map(schedule_dict)

To conduct navigation based on best parameters, the original dataframe copy above was modified to schedule the specified ratio of patients-to-techs.

In [84]:
movements = []
current_techs_col = []

for date in new_patients_df.visit_date.unique():
    date_df = new_patients_df[new_patients_df.visit_date == date].copy()

    # Modify scheduled number of technicians to begin the day
    date_df['new_num_techs'] = date_df['assigned_num_techs'] - 1

    # Instantiate and execute navigation
    nav = TecNav(date_df, clinics_df, model)
    nav.execute_navigation()

    # Retrieve technician count at each instance of time from navigation
    current_techs_col.extend(nav.current_num_techs_col)

    # Retrieve each movement
    movements.extend(nav.movements)

08:46:13 - Edgewater Clinic needs a technician
- Availability:  ['Wheatridge', 'Lakewood', 'Rino']
- Assessing if Wheatridge is a feasible location to pull technician from.
- Pull technician from nearest clinic: Wheatridge, 2 available
- Technician from Wheatridge left at 08:49:04
- Technician from Wheatridge arrived at Edgewater at 08:57:10
- Edgewater: before count = 1 | after count = 2
- Wheatridge: before count = 3 | after count = 2

10:28:39 - Rino Clinic needs a technician
- Availability:  ['Denver', 'Wheatridge']
- Assessing if Denver is a feasible location to pull technician from.
  Denver only has 1 technician available 
  Deploy ML model to assess if transfer is feasible:
    - Predicted amount needed = 2 | Current amount needed = 1
        - ML model recommends no transfer from Denver
- Assessing if Wheatridge is a feasible location to pull technician from.
  Wheatridge only has 1 technician available 
  Deploy ML model to assess if transfer is feasible:
    - Predicted amou

#### Visualize the dynamic technician count due to navigation:

In [85]:
# Define date of interest to study further
date_of_interest = '2022-05-31'

A date can be manually selected above to re-run and generate the visuals below.

In [86]:
new_patients_df['current_num_techs'] = current_techs_col

# Create iterable objects that are desired for toggle menus
locations = new_patients_df.visit_location.unique().tolist()

fig = make_subplots(
rows=5, cols=1, 
specs=[[{'type':'xy'}], [{'type':'xy'}], [{'type':'xy'}], [{'type':'xy'}], [{'type':'xy'}]], 
subplot_titles=["Denver", "Edgewater", "Wheatridge", "RINO", "Lakewood"]
)

# Plot for each location
for i in range(5):
    
    location = locations[i]
    df = new_patients_df.copy()
    df = df[df.visit_date.astype('str') == date_of_interest]
    
    # Convert specific times to grouped versions
    df['checkin_time'] = df.checkin_time.astype('str').apply(lambda x: x[:-3])

    # Create subset data for desired date and the two locations to compare
    df = df[(df.visit_location == location)]

    # Construct lineplot for tech-count by location & time
    line1 = go.Scatter(
        x=df['checkin_time'], y=df['assigned_num_techs'], 
        name=f'Original Scheduled Number of Techs @ {location.capitalize()}', marker_color='yellow', line = dict(color='blue', width=4, dash='dash'), 
        mode='lines', legendgroup=i+1
    )
    line2 = go.Scatter(
        x=df['checkin_time'], y=df['current_num_techs'], 
        name=f'Current Number of Techs @ {location.capitalize()}', marker_color='green', legendgroup=i+1, mode='lines'
    )
    line3 = go.Scatter(
        x=df['checkin_time'], y=df['needed_num_techs'], 
        name=f'Needed Number of Techs @ {location.capitalize()}', marker_color='red', legendgroup=i+1, mode='lines'
    )

    # Add subplots to figure object
    fig.add_trace(line1, row=i+1, col=1)
    fig.add_trace(line2, row=i+1, col=1)
    fig.add_trace(line3, row=i+1, col=1)

# Output figure with custom modifications
fig.update_traces(opacity=0.3)
fig.update_layout(height=1500, width=1200, showlegend=True, legend_tracegroupgap=250)
fig.show()

In these visuals, we can see TecNav's optimization bridging the gap between needed and current number of technicians throughout the day. This will be included as part of the dashboard to help clients understand how the application can fulfill their needs.

#### Compute client-based success metrics:

In [87]:
clinic_distances = {
    ('denver', 'rino'): 2, 
    ('wheatridge', 'edgewater'): 2,
    ('rino', 'denver'): 1.9, 
    ('edgewater', 'wheatridge'): 2,
    ('wheatridge', 'lakewood'): 4.8, 
    ('rino', 'wheatridge'): 7.5,
    ('edgewater', 'denver'): 5,  
    ('lakewood', 'wheatridge'): 12,
    ('wheatridge', 'denver'): 6.3,  
    ('edgewater', 'lakewood'): 4.4,
    ('denver', 'lakewood'): 8,  
    ('lakewood', 'edgewater'): 4.3,
    ('wheatridge', 'rino'): 7.8,  
    ('rino', 'lakewood'): 10.7,
    ('denver', 'edgewater'): 5.1,  
    ('lakewood', 'rino'): 11,
    ('rino', 'edgewater'): 7.8,  
    ('edgewater', 'rino'): 7.7,
    ('lakewood', 'denver'): 7.5,   
    ('denver', 'wheatridge'): 6.3
}
print('Number of movements total (May 2022):', len(movements))
distances = pd.DataFrame(pd.Series(movements).value_counts()).reset_index(drop=False).rename(columns={'index': 'routes', 0: 'count'})
distances['dist'] = distances.routes.map(clinic_distances)
distances['cum_route_dist'] = distances[['count', 'dist']].apply(lambda x: x[0] * x[1], axis=1)
total_distance = round(distances.cum_route_dist.sum())
print(total_distance)
display(distances)

Number of movements total (May 2022): 241
1372


routes  count  dist  cum_route_dist
0   (wheatridge, edgewater)     23   2.0            46.0
1            (denver, rino)     23   2.0            46.0
2    (lakewood, wheatridge)     21  12.0           252.0
3    (wheatridge, lakewood)     19   4.8            91.2
4        (denver, lakewood)     16   8.0           128.0
5   (edgewater, wheatridge)     15   2.0            30.0
6            (rino, denver)     13   1.9            24.7
7        (wheatridge, rino)     12   7.8            93.6
8     (edgewater, lakewood)     12   4.4            52.8
9     (lakewood, edgewater)     12   4.3            51.6
10       (rino, wheatridge)     11   7.5            82.5
11      (edgewater, denver)     10   5.0            50.0
12       (lakewood, denver)      9   7.5            67.5
13         (lakewood, rino)      9  11.0            99.0
14     (denver, wheatridge)      9   6.3            56.7
15     (wheatridge, denver)      7   6.3            44.1
16        (rino, edgewater)      6   7.8            46.8
17      (denver, edgewater)      5   5.1            25.5
18         (rino, lakewood)      5  10.7            53.5
19        (edgewater, rino)      4   7.7            30.8

The distances were gathered (Google Maps) for each clinic pair to compute the cumulative distance traveled by technicians over the entire month (May 2022). This information will aid in calculating the final savings below.

In [88]:
avg_gas_price =  4.23  # Avg gas price in Denver (May 2022)
avg_mpg = 24.2  # US Dept of Energy

print('Gas money reimbursements to technicians for navigation moves (for May 2022): ', round(total_distance / avg_mpg * avg_gas_price, 2))

Gas money reimbursements to technicians for navigation moves (for May 2022):  239.82


For these 5 clinics in the region, it is feasible to schedule 5 technicians less per day and still maintain productivity through TecNav. With an average wage of $21/hr for technicians, this would equate to $91980 saved in compensation over an entire year ($7665/month) for each clinic. Note: These savings only account for the wage compensation and not savings on any additional employee benefits. There were 241 amount of moves that occured through TecNav in a single month--this would lead to an estimated $240 of gas compensation per month, equating to about $2880 per year. So accounting for this, the urgent care chain would save about $89100 for an entire year. This money could be instead invested in further advanced diagnostic tools & imaging equipment that could help the client offer a more comprehensive set of health services or help minimize medical costs for the patients--both of which align with the overall mission of the client's urgent care chain. 

---
---

## 4D: Launch Demo

**Objective**: Launch interactive dashboard to enable user-based navigation simulation of any past day:

---

In [89]:
# Run navigation on specified data and parameters
# !python uc_navigator.py new -s -1 -r 3

In [91]:
# Launch dashboard
!streamlit run TecNav_Demo.py


  You can now view your Streamlit app in your browser.

  Local URL: http://localhost:8501
  Network URL: http://192.168.0.6:8501

  For better performance, install the Watchdog module:

  $ xcode-select --install
  $ pip install watchdog
            
2022-05-28 13:55:18.977 NumExpr defaulting to 8 threads.
^C
  Stopping...
